In [1]:
import pandas as pd
from rdkit import Chem
from rdkit.ML.Descriptors.Descriptors import DescriptorCalculator
from rdkit.ML.Descriptors.MoleculeDescriptors import MolecularDescriptorCalculator
import numpy as np
import catboost
from tqdm import tqdm
from sklearn import metrics
from sklearn.model_selection import cross_val_score, KFold, train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split, RandomizedSearchCV
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error
from statistics import mean, stdev
from platform import python_version
print(python_version())

3.8.16


In [2]:
df = pd.read_excel("Condensation_reactions.xls")

In [3]:
df['SMILES'] = df['SMILES'].replace('>>', '.', regex=True)

In [4]:
descriptor_names = list(Chem.rdMolDescriptors.Properties.GetAvailableProperties())
descriptor_names.remove('exactmw')
def descriptor(descriptor:str, smi:str)->float:
    get_descriptors = Chem.rdMolDescriptors.Properties([descriptor])
    try:
        return get_descriptors.ComputeProperties(Chem.MolFromSmiles(smi))[0]
    except:
        return None

In [5]:
for name in tqdm(descriptor_names):
     df[name] = df['SMILES'].apply(lambda x: descriptor(name, x))

  0%|                                                                          | 0/42 [00:00<?, ?it/s][10:59:40] Explicit valence for atom # 26 H, 2, is greater than permitted
[10:59:40] Explicit valence for atom # 26 H, 2, is greater than permitted
[10:59:40] Explicit valence for atom # 0 O, 3, is greater than permitted
[10:59:40] Explicit valence for atom # 10 O, 3, is greater than permitted
  2%|█▌                                                                | 1/42 [00:00<00:38,  1.06it/s][10:59:40] Explicit valence for atom # 26 H, 2, is greater than permitted
[10:59:41] Explicit valence for atom # 26 H, 2, is greater than permitted
[10:59:41] Explicit valence for atom # 0 O, 3, is greater than permitted
[10:59:41] Explicit valence for atom # 10 O, 3, is greater than permitted
  5%|███▏                                                              | 2/42 [00:01<00:34,  1.17it/s][10:59:41] Explicit valence for atom # 26 H, 2, is greater than permitted
[10:59:41] Explicit valence fo

 50%|████████████████████████████████▌                                | 21/42 [00:18<00:18,  1.13it/s][10:59:58] Explicit valence for atom # 26 H, 2, is greater than permitted
[10:59:58] Explicit valence for atom # 26 H, 2, is greater than permitted
[10:59:58] Explicit valence for atom # 0 O, 3, is greater than permitted
[10:59:59] Explicit valence for atom # 10 O, 3, is greater than permitted
 52%|██████████████████████████████████                               | 22/42 [00:19<00:17,  1.13it/s][10:59:59] Explicit valence for atom # 26 H, 2, is greater than permitted
[10:59:59] Explicit valence for atom # 26 H, 2, is greater than permitted
[10:59:59] Explicit valence for atom # 0 O, 3, is greater than permitted
[11:00:00] Explicit valence for atom # 10 O, 3, is greater than permitted
 55%|███████████████████████████████████▌                             | 23/42 [00:20<00:16,  1.13it/s][11:00:00] Explicit valence for atom # 26 H, 2, is greater than permitted
[11:00:00] Explicit valence fo

100%|█████████████████████████████████████████████████████████████████| 42/42 [00:44<00:00,  1.07s/it]


In [6]:
data=df.dropna()
data.reset_index(drop=True , inplace=True)
data.shape

(1245, 46)

In [7]:
descriptors=data.drop(["SMILES", 'yield', 'Ind'], axis=1)

In [8]:
# descriptor filtering
corr = descriptors.copy().corr()
threshold = 0.9
for index in corr.index:
    corr.loc[index, index] = 0
descriptors_not_correlated = corr[(corr<=threshold)].dropna().index.tolist()
print('Number of descriptors:', len(descriptors_not_correlated)-1)

Number of descriptors: 13


In [9]:
y = data['yield']
y = y.astype(float)
X = descriptors.loc[:, descriptors_not_correlated]

In [10]:
# The "reaction" strategy
# Random Forest Regression
rmse_scores = []
r2_scores = []
for i in range(10):
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=i)
    model = RandomForestRegressor(n_estimators=800, max_depth=8) # Hyperparameter optimization was carried out in the Optuna
    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    rmse_scores.append(rmse)
    r2 = r2_score(y_test, y_pred)
    r2_scores.append(r2)
    print(f"Iteration {i}: RMSE = {rmse:.3f}, R^2  = {r2:.3f}")
    
print("\nAverage performance of test set at 10 split")
print("Metric\tavg\tstdev")
print("R^2\t%.2f\t%.2f" % (mean(r2_scores), stdev(r2_scores)))
print("RMSE\t%.2f\t%.2f" % (mean(rmse_scores), stdev(rmse_scores)))

Iteration 0: RMSE = 15.753, R^2  = 0.471
Iteration 1: RMSE = 13.837, R^2  = 0.564
Iteration 2: RMSE = 13.530, R^2  = 0.585
Iteration 3: RMSE = 13.104, R^2  = 0.617
Iteration 4: RMSE = 14.277, R^2  = 0.525
Iteration 5: RMSE = 13.711, R^2  = 0.651
Iteration 6: RMSE = 13.592, R^2  = 0.556
Iteration 7: RMSE = 14.490, R^2  = 0.532
Iteration 8: RMSE = 13.666, R^2  = 0.555
Iteration 9: RMSE = 13.877, R^2  = 0.559

Average performance of test set at 10 split
Metric	avg	stdev
R^2	0.56	0.05
RMSE	13.98	0.73


In [11]:
# Statistics for the training set with 5CV
r2_scores = []
rmse_scores = []
for i in range(10):
    X_tr, X_t, y_tr, y_t = train_test_split(X, y, test_size=0.2, random_state=i)
    X_tr.reset_index(drop=True , inplace=True)
    y_tr.reset_index(drop=True , inplace=True)
    cv = KFold(n_splits=5, shuffle=True, random_state=1)
    y_pred, y_true = [], []
    for train_index, test_index in cv.split(X_tr):
        X_train = X_tr.loc[train_index].values
        X_test = X_tr.loc[test_index].values
        y_train = y_tr.loc[train_index].values
        y_test = y_tr.loc[test_index].values

        model = RandomForestRegressor(n_estimators=800, max_depth=8)
        model.fit(X_train, y_train)
        y_pred.extend(model.predict(X_test))
        y_true.extend(y_test)

    r2_scores.append(metrics.r2_score(y_true, y_pred))
    rmse_scores.append(metrics.mean_squared_error(y_true, y_pred, squared=False))
      
print("\nAverage performance of 5CV")
print("Metric\tavg\tstdev")
print("R^2\t%.2f\t%.2f" % (mean(r2_scores), stdev(r2_scores)))
print("RMSE\t%.2f\t%.2f" % (mean(rmse_scores), stdev(rmse_scores)))        


Average performance of 5CV
Metric	avg	stdev
R^2	0.55	0.02
RMSE	14.26	0.27


In [12]:
# catBoost

In [13]:
rmse_scores = []
r2_scores = []
for i in range(10):
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=i)
    model = catboost.CatBoostRegressor(learning_rate=0.02, l2_leaf_reg=9.5, depth=7) # Hyperparameter optimization was carried out in the Optuna
    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    rmse_scores.append(rmse)
    r2 = r2_score(y_test, y_pred)
    r2_scores.append(r2)
    print(f"Iteration {i}: RMSE = {rmse:.3f}, R2 = {r2:.3f}")

0:	learn: 21.0924667	total: 55.2ms	remaining: 55.1s
1:	learn: 20.9557565	total: 60.8ms	remaining: 30.3s
2:	learn: 20.7916821	total: 63.9ms	remaining: 21.2s
3:	learn: 20.6451382	total: 67.1ms	remaining: 16.7s
4:	learn: 20.5157515	total: 69.6ms	remaining: 13.9s
5:	learn: 20.3830767	total: 71.8ms	remaining: 11.9s
6:	learn: 20.2534814	total: 73.8ms	remaining: 10.5s
7:	learn: 20.1429759	total: 76.1ms	remaining: 9.44s
8:	learn: 19.9973205	total: 78.1ms	remaining: 8.6s
9:	learn: 19.8505291	total: 80.1ms	remaining: 7.93s
10:	learn: 19.7182355	total: 82ms	remaining: 7.37s
11:	learn: 19.5885760	total: 84.1ms	remaining: 6.93s
12:	learn: 19.4810419	total: 86ms	remaining: 6.53s
13:	learn: 19.3732942	total: 87.9ms	remaining: 6.19s
14:	learn: 19.2660082	total: 89.8ms	remaining: 5.9s
15:	learn: 19.1451827	total: 91.7ms	remaining: 5.64s
16:	learn: 19.0381590	total: 93.5ms	remaining: 5.41s
17:	learn: 18.9329425	total: 95.3ms	remaining: 5.2s
18:	learn: 18.8159347	total: 97.1ms	remaining: 5.01s
19:	learn:

213:	learn: 13.5176873	total: 444ms	remaining: 1.63s
214:	learn: 13.5124838	total: 446ms	remaining: 1.63s
215:	learn: 13.4999899	total: 447ms	remaining: 1.62s
216:	learn: 13.4957394	total: 449ms	remaining: 1.62s
217:	learn: 13.4836252	total: 452ms	remaining: 1.62s
218:	learn: 13.4779299	total: 454ms	remaining: 1.62s
219:	learn: 13.4705800	total: 456ms	remaining: 1.61s
220:	learn: 13.4684933	total: 458ms	remaining: 1.61s
221:	learn: 13.4604363	total: 459ms	remaining: 1.61s
222:	learn: 13.4570253	total: 461ms	remaining: 1.6s
223:	learn: 13.4478482	total: 462ms	remaining: 1.6s
224:	learn: 13.4461577	total: 464ms	remaining: 1.6s
225:	learn: 13.4381789	total: 465ms	remaining: 1.59s
226:	learn: 13.4324520	total: 467ms	remaining: 1.59s
227:	learn: 13.4236254	total: 469ms	remaining: 1.59s
228:	learn: 13.4161609	total: 470ms	remaining: 1.58s
229:	learn: 13.4097424	total: 472ms	remaining: 1.58s
230:	learn: 13.4059376	total: 474ms	remaining: 1.58s
231:	learn: 13.4003429	total: 475ms	remaining: 1.

457:	learn: 12.4882000	total: 834ms	remaining: 987ms
458:	learn: 12.4786712	total: 836ms	remaining: 985ms
459:	learn: 12.4778978	total: 837ms	remaining: 983ms
460:	learn: 12.4754976	total: 839ms	remaining: 981ms
461:	learn: 12.4746183	total: 840ms	remaining: 979ms
462:	learn: 12.4743388	total: 842ms	remaining: 976ms
463:	learn: 12.4730234	total: 843ms	remaining: 974ms
464:	learn: 12.4725962	total: 844ms	remaining: 972ms
465:	learn: 12.4595766	total: 846ms	remaining: 970ms
466:	learn: 12.4569862	total: 848ms	remaining: 968ms
467:	learn: 12.4556272	total: 850ms	remaining: 966ms
468:	learn: 12.4533846	total: 852ms	remaining: 964ms
469:	learn: 12.4520835	total: 853ms	remaining: 962ms
470:	learn: 12.4505870	total: 855ms	remaining: 960ms
471:	learn: 12.4478716	total: 856ms	remaining: 958ms
472:	learn: 12.4462386	total: 858ms	remaining: 956ms
473:	learn: 12.4400895	total: 860ms	remaining: 954ms
474:	learn: 12.4383078	total: 861ms	remaining: 952ms
475:	learn: 12.4374265	total: 863ms	remaining:

693:	learn: 11.5365589	total: 1.23s	remaining: 541ms
694:	learn: 11.5355655	total: 1.23s	remaining: 539ms
695:	learn: 11.5303953	total: 1.23s	remaining: 537ms
696:	learn: 11.5217388	total: 1.23s	remaining: 535ms
697:	learn: 11.5196472	total: 1.23s	remaining: 534ms
698:	learn: 11.5165337	total: 1.24s	remaining: 532ms
699:	learn: 11.5129250	total: 1.24s	remaining: 530ms
700:	learn: 11.5120436	total: 1.24s	remaining: 528ms
701:	learn: 11.5070754	total: 1.24s	remaining: 527ms
702:	learn: 11.5016321	total: 1.24s	remaining: 525ms
703:	learn: 11.4942191	total: 1.24s	remaining: 523ms
704:	learn: 11.4935977	total: 1.25s	remaining: 521ms
705:	learn: 11.4852399	total: 1.25s	remaining: 520ms
706:	learn: 11.4801856	total: 1.25s	remaining: 518ms
707:	learn: 11.4766120	total: 1.25s	remaining: 516ms
708:	learn: 11.4692732	total: 1.25s	remaining: 515ms
709:	learn: 11.4628486	total: 1.25s	remaining: 513ms
710:	learn: 11.4593982	total: 1.26s	remaining: 511ms
711:	learn: 11.4553760	total: 1.26s	remaining:

920:	learn: 10.7713004	total: 1.61s	remaining: 139ms
921:	learn: 10.7707709	total: 1.62s	remaining: 137ms
922:	learn: 10.7634315	total: 1.62s	remaining: 135ms
923:	learn: 10.7608004	total: 1.62s	remaining: 133ms
924:	learn: 10.7592769	total: 1.62s	remaining: 131ms
925:	learn: 10.7521012	total: 1.62s	remaining: 130ms
926:	learn: 10.7455292	total: 1.62s	remaining: 128ms
927:	learn: 10.7402815	total: 1.63s	remaining: 126ms
928:	learn: 10.7383473	total: 1.63s	remaining: 124ms
929:	learn: 10.7363800	total: 1.63s	remaining: 123ms
930:	learn: 10.7339068	total: 1.63s	remaining: 121ms
931:	learn: 10.7318926	total: 1.63s	remaining: 119ms
932:	learn: 10.7310134	total: 1.65s	remaining: 118ms
933:	learn: 10.7273171	total: 1.65s	remaining: 117ms
934:	learn: 10.7229583	total: 1.65s	remaining: 115ms
935:	learn: 10.7217049	total: 1.65s	remaining: 113ms
936:	learn: 10.7200528	total: 1.66s	remaining: 111ms
937:	learn: 10.7183886	total: 1.66s	remaining: 109ms
938:	learn: 10.7164065	total: 1.66s	remaining:

...

12:	learn: 19.7479290	total: 22.5ms	remaining: 1.71s
13:	learn: 19.6204067	total: 24.5ms	remaining: 1.73s
14:	learn: 19.5080775	total: 26.1ms	remaining: 1.71s
15:	learn: 19.3956842	total: 27.8ms	remaining: 1.71s
16:	learn: 19.2866713	total: 29.3ms	remaining: 1.7s
17:	learn: 19.1856419	total: 30.9ms	remaining: 1.69s
18:	learn: 19.0759762	total: 32.6ms	remaining: 1.68s
19:	learn: 18.9851486	total: 34.2ms	remaining: 1.68s
20:	learn: 18.8809621	total: 35.9ms	remaining: 1.68s
21:	learn: 18.7767500	total: 37.5ms	remaining: 1.67s
22:	learn: 18.6973906	total: 39.2ms	remaining: 1.66s
23:	learn: 18.5939411	total: 40.6ms	remaining: 1.65s
24:	learn: 18.5017659	total: 41.6ms	remaining: 1.62s
25:	learn: 18.4113847	total: 43.3ms	remaining: 1.62s
26:	learn: 18.3170121	total: 45ms	remaining: 1.62s
27:	learn: 18.2409279	total: 46.8ms	remaining: 1.62s
28:	learn: 18.1492097	total: 48.3ms	remaining: 1.62s
29:	learn: 18.0588915	total: 49.9ms	remaining: 1.61s
30:	learn: 17.9723740	total: 51.7ms	remaining: 1.

261:	learn: 13.5016521	total: 413ms	remaining: 1.16s
262:	learn: 13.5002243	total: 415ms	remaining: 1.16s
263:	learn: 13.4980494	total: 416ms	remaining: 1.16s
264:	learn: 13.4900810	total: 418ms	remaining: 1.16s
265:	learn: 13.4823972	total: 420ms	remaining: 1.16s
266:	learn: 13.4780245	total: 421ms	remaining: 1.16s
267:	learn: 13.4762963	total: 423ms	remaining: 1.15s
268:	learn: 13.4672307	total: 424ms	remaining: 1.15s
269:	learn: 13.4582140	total: 426ms	remaining: 1.15s
270:	learn: 13.4561562	total: 428ms	remaining: 1.15s
271:	learn: 13.4516132	total: 429ms	remaining: 1.15s
272:	learn: 13.4480404	total: 431ms	remaining: 1.15s
273:	learn: 13.4436545	total: 432ms	remaining: 1.15s
274:	learn: 13.4385149	total: 434ms	remaining: 1.14s
275:	learn: 13.4327149	total: 436ms	remaining: 1.14s
276:	learn: 13.4274862	total: 437ms	remaining: 1.14s
277:	learn: 13.4244706	total: 439ms	remaining: 1.14s
278:	learn: 13.4206412	total: 440ms	remaining: 1.14s
279:	learn: 13.4133583	total: 442ms	remaining:

505:	learn: 12.4416854	total: 802ms	remaining: 783ms
506:	learn: 12.4325887	total: 804ms	remaining: 782ms
507:	learn: 12.4249766	total: 806ms	remaining: 781ms
508:	learn: 12.4206479	total: 808ms	remaining: 779ms
509:	learn: 12.4138705	total: 810ms	remaining: 778ms
510:	learn: 12.4130731	total: 811ms	remaining: 776ms
511:	learn: 12.4059857	total: 813ms	remaining: 775ms
512:	learn: 12.4053428	total: 815ms	remaining: 774ms
513:	learn: 12.4005413	total: 817ms	remaining: 772ms
514:	learn: 12.3999779	total: 819ms	remaining: 771ms
515:	learn: 12.3962144	total: 820ms	remaining: 769ms
516:	learn: 12.3920055	total: 822ms	remaining: 768ms
517:	learn: 12.3861332	total: 824ms	remaining: 767ms
518:	learn: 12.3851666	total: 826ms	remaining: 765ms
519:	learn: 12.3842951	total: 827ms	remaining: 764ms
520:	learn: 12.3820703	total: 829ms	remaining: 762ms
521:	learn: 12.3804096	total: 831ms	remaining: 761ms
522:	learn: 12.3777272	total: 833ms	remaining: 760ms
523:	learn: 12.3764149	total: 835ms	remaining:

734:	learn: 11.4665513	total: 1.19s	remaining: 429ms
735:	learn: 11.4660960	total: 1.19s	remaining: 428ms
736:	learn: 11.4617354	total: 1.19s	remaining: 426ms
737:	learn: 11.4574420	total: 1.2s	remaining: 425ms
738:	learn: 11.4526727	total: 1.2s	remaining: 423ms
739:	learn: 11.4440679	total: 1.2s	remaining: 421ms
740:	learn: 11.4373053	total: 1.2s	remaining: 420ms
741:	learn: 11.4341305	total: 1.2s	remaining: 418ms
742:	learn: 11.4294499	total: 1.2s	remaining: 417ms
743:	learn: 11.4233886	total: 1.21s	remaining: 415ms
744:	learn: 11.4186718	total: 1.21s	remaining: 413ms
745:	learn: 11.4158147	total: 1.21s	remaining: 412ms
746:	learn: 11.4131512	total: 1.21s	remaining: 410ms
747:	learn: 11.4064671	total: 1.21s	remaining: 408ms
748:	learn: 11.4002944	total: 1.21s	remaining: 407ms
749:	learn: 11.3996884	total: 1.22s	remaining: 405ms
750:	learn: 11.3946459	total: 1.22s	remaining: 404ms
751:	learn: 11.3932177	total: 1.22s	remaining: 402ms
752:	learn: 11.3888161	total: 1.22s	remaining: 400ms

973:	learn: 10.6573357	total: 1.58s	remaining: 42.2ms
974:	learn: 10.6564343	total: 1.58s	remaining: 40.6ms
975:	learn: 10.6508230	total: 1.58s	remaining: 39ms
976:	learn: 10.6459087	total: 1.58s	remaining: 37.3ms
977:	learn: 10.6420980	total: 1.59s	remaining: 35.7ms
978:	learn: 10.6402134	total: 1.59s	remaining: 34.1ms
979:	learn: 10.6397849	total: 1.59s	remaining: 32.5ms
980:	learn: 10.6332109	total: 1.59s	remaining: 30.8ms
981:	learn: 10.6290010	total: 1.59s	remaining: 29.2ms
982:	learn: 10.6268825	total: 1.59s	remaining: 27.6ms
983:	learn: 10.6264611	total: 1.6s	remaining: 26ms
984:	learn: 10.6261255	total: 1.6s	remaining: 24.3ms
985:	learn: 10.6254912	total: 1.6s	remaining: 22.7ms
986:	learn: 10.6238405	total: 1.6s	remaining: 21.1ms
987:	learn: 10.6199064	total: 1.6s	remaining: 19.5ms
988:	learn: 10.6193489	total: 1.6s	remaining: 17.9ms
989:	learn: 10.6188963	total: 1.61s	remaining: 16.2ms
990:	learn: 10.6168510	total: 1.61s	remaining: 14.6ms
991:	learn: 10.6124347	total: 1.61s	re

In [14]:
print("\nAverage performance of test set at 10 split")
print("Metric\tavg\tstdev")
print("R^2\t%.2f\t%.2f" % (mean(r2_scores), stdev(r2_scores)))
print("RMSE\t%.2f\t%.2f" % (mean(rmse_scores), stdev(rmse_scores)))


Average performance of test set at 10 split
Metric	avg	stdev
R^2	0.57	0.04
RMSE	13.87	0.66


In [15]:
# Statistics for the training set with 5CV
r2_scores = []
rmse_scores = []
for i in range(10):
    X_tr, X_t, y_tr, y_t = train_test_split(X, y, test_size=0.2, random_state=i)
    X_tr.reset_index(drop=True , inplace=True)
    y_tr.reset_index(drop=True , inplace=True)
    cv = KFold(n_splits=5, shuffle=True, random_state=1)
    y_pred, y_true = [], []
    for train_index, test_index in cv.split(X_tr):
        X_train = X_tr.loc[train_index].values
        X_test = X_tr.loc[test_index].values
        y_train = y_tr.loc[train_index].values
        y_test = y_tr.loc[test_index].values

        model = catboost.CatBoostRegressor(learning_rate=0.02, l2_leaf_reg=9.5, depth=7)
        model.fit(X_train, y_train)
        y_pred.extend(model.predict(X_test))
        y_true.extend(y_test)

    r2_scores.append(metrics.r2_score(y_true, y_pred))
    rmse_scores.append(metrics.mean_squared_error(y_true, y_pred, squared=False))

0:	learn: 20.9514783	total: 2.8ms	remaining: 2.8s
1:	learn: 20.8284968	total: 5.67ms	remaining: 2.83s
2:	learn: 20.6856481	total: 8.2ms	remaining: 2.72s
3:	learn: 20.5600675	total: 10ms	remaining: 2.5s
4:	learn: 20.4201852	total: 12.3ms	remaining: 2.45s
5:	learn: 20.2923287	total: 14.5ms	remaining: 2.39s
6:	learn: 20.1809612	total: 16.9ms	remaining: 2.4s
7:	learn: 20.0790520	total: 19.2ms	remaining: 2.38s
8:	learn: 19.9288751	total: 21.5ms	remaining: 2.37s
9:	learn: 19.8303736	total: 23.5ms	remaining: 2.33s
10:	learn: 19.7128803	total: 25.6ms	remaining: 2.3s
11:	learn: 19.5963217	total: 27.8ms	remaining: 2.29s
12:	learn: 19.4926107	total: 29.8ms	remaining: 2.26s
13:	learn: 19.3993951	total: 31.7ms	remaining: 2.23s
14:	learn: 19.2939379	total: 33.6ms	remaining: 2.21s
15:	learn: 19.1772159	total: 35.9ms	remaining: 2.21s
16:	learn: 19.0885162	total: 38.1ms	remaining: 2.2s
17:	learn: 18.9880024	total: 39.9ms	remaining: 2.18s
18:	learn: 18.8992586	total: 41.6ms	remaining: 2.15s
19:	learn: 1

226:	learn: 13.5138716	total: 392ms	remaining: 1.33s
227:	learn: 13.5069089	total: 394ms	remaining: 1.33s
228:	learn: 13.5018684	total: 396ms	remaining: 1.33s
229:	learn: 13.4920824	total: 398ms	remaining: 1.33s
230:	learn: 13.4841526	total: 400ms	remaining: 1.33s
231:	learn: 13.4738994	total: 401ms	remaining: 1.33s
232:	learn: 13.4680122	total: 403ms	remaining: 1.32s
233:	learn: 13.4612269	total: 404ms	remaining: 1.32s
234:	learn: 13.4543467	total: 406ms	remaining: 1.32s
235:	learn: 13.4508650	total: 408ms	remaining: 1.32s
236:	learn: 13.4381732	total: 409ms	remaining: 1.32s
237:	learn: 13.4339649	total: 411ms	remaining: 1.31s
238:	learn: 13.4266679	total: 412ms	remaining: 1.31s
239:	learn: 13.4212441	total: 414ms	remaining: 1.31s
240:	learn: 13.4183859	total: 416ms	remaining: 1.31s
241:	learn: 13.4125886	total: 417ms	remaining: 1.31s
242:	learn: 13.4059316	total: 419ms	remaining: 1.3s
243:	learn: 13.3959063	total: 420ms	remaining: 1.3s
244:	learn: 13.3924389	total: 422ms	remaining: 1

479:	learn: 12.2821858	total: 784ms	remaining: 849ms
480:	learn: 12.2813018	total: 785ms	remaining: 847ms
481:	learn: 12.2795685	total: 788ms	remaining: 847ms
482:	learn: 12.2784055	total: 790ms	remaining: 845ms
483:	learn: 12.2775617	total: 791ms	remaining: 844ms
484:	learn: 12.2763372	total: 795ms	remaining: 845ms
485:	learn: 12.2674717	total: 797ms	remaining: 843ms
486:	learn: 12.2662689	total: 798ms	remaining: 841ms
487:	learn: 12.2653235	total: 800ms	remaining: 840ms
488:	learn: 12.2642130	total: 802ms	remaining: 838ms
489:	learn: 12.2559962	total: 803ms	remaining: 836ms
490:	learn: 12.2552790	total: 805ms	remaining: 835ms
491:	learn: 12.2475395	total: 807ms	remaining: 833ms
492:	learn: 12.2468623	total: 808ms	remaining: 831ms
493:	learn: 12.2463553	total: 810ms	remaining: 829ms
494:	learn: 12.2394751	total: 811ms	remaining: 828ms
495:	learn: 12.2327230	total: 813ms	remaining: 826ms
496:	learn: 12.2280046	total: 814ms	remaining: 824ms
497:	learn: 12.2270576	total: 816ms	remaining:

704:	learn: 11.4459060	total: 1.17s	remaining: 488ms
705:	learn: 11.4437720	total: 1.17s	remaining: 487ms
706:	learn: 11.4417428	total: 1.17s	remaining: 485ms
707:	learn: 11.4374619	total: 1.17s	remaining: 484ms
708:	learn: 11.4309496	total: 1.17s	remaining: 482ms
709:	learn: 11.4215352	total: 1.18s	remaining: 480ms
710:	learn: 11.4183118	total: 1.18s	remaining: 479ms
711:	learn: 11.4084847	total: 1.18s	remaining: 477ms
712:	learn: 11.4074772	total: 1.18s	remaining: 476ms
713:	learn: 11.4056644	total: 1.18s	remaining: 474ms
714:	learn: 11.4024213	total: 1.18s	remaining: 472ms
715:	learn: 11.4018056	total: 1.19s	remaining: 471ms
716:	learn: 11.3959343	total: 1.19s	remaining: 469ms
717:	learn: 11.3923380	total: 1.19s	remaining: 467ms
718:	learn: 11.3895209	total: 1.19s	remaining: 466ms
719:	learn: 11.3887439	total: 1.19s	remaining: 464ms
720:	learn: 11.3859035	total: 1.2s	remaining: 463ms
721:	learn: 11.3787833	total: 1.2s	remaining: 461ms
722:	learn: 11.3772185	total: 1.2s	remaining: 45

942:	learn: 10.6090195	total: 1.55s	remaining: 94ms
943:	learn: 10.6074407	total: 1.56s	remaining: 92.3ms
944:	learn: 10.6067153	total: 1.56s	remaining: 90.7ms
945:	learn: 10.6012401	total: 1.56s	remaining: 89ms
946:	learn: 10.6007709	total: 1.56s	remaining: 87.4ms
947:	learn: 10.5999674	total: 1.56s	remaining: 85.7ms
948:	learn: 10.5986342	total: 1.56s	remaining: 84.1ms
949:	learn: 10.5939551	total: 1.57s	remaining: 82.4ms
950:	learn: 10.5924005	total: 1.57s	remaining: 80.8ms
951:	learn: 10.5864227	total: 1.57s	remaining: 79.1ms
952:	learn: 10.5851850	total: 1.57s	remaining: 77.5ms
953:	learn: 10.5839527	total: 1.57s	remaining: 75.8ms
954:	learn: 10.5812947	total: 1.57s	remaining: 74.2ms
955:	learn: 10.5808390	total: 1.57s	remaining: 72.5ms
956:	learn: 10.5794564	total: 1.58s	remaining: 70.9ms
957:	learn: 10.5708149	total: 1.58s	remaining: 69.2ms
958:	learn: 10.5669489	total: 1.58s	remaining: 67.6ms
959:	learn: 10.5606773	total: 1.58s	remaining: 65.9ms
960:	learn: 10.5566422	total: 1.

...

944:	learn: 10.7935304	total: 1.82s	remaining: 106ms
945:	learn: 10.7897884	total: 1.82s	remaining: 104ms
946:	learn: 10.7894848	total: 1.82s	remaining: 102ms
947:	learn: 10.7888182	total: 1.82s	remaining: 100ms
948:	learn: 10.7877135	total: 1.82s	remaining: 98.1ms
949:	learn: 10.7832480	total: 1.83s	remaining: 96.1ms
950:	learn: 10.7822726	total: 1.83s	remaining: 94.2ms
951:	learn: 10.7774080	total: 1.83s	remaining: 92.2ms
952:	learn: 10.7750818	total: 1.83s	remaining: 90.3ms
953:	learn: 10.7702618	total: 1.83s	remaining: 88.4ms
954:	learn: 10.7678157	total: 1.83s	remaining: 86.4ms
955:	learn: 10.7671231	total: 1.84s	remaining: 84.5ms
956:	learn: 10.7668438	total: 1.84s	remaining: 82.6ms
957:	learn: 10.7592680	total: 1.84s	remaining: 80.6ms
958:	learn: 10.7589484	total: 1.84s	remaining: 78.7ms
959:	learn: 10.7554626	total: 1.84s	remaining: 76.8ms
960:	learn: 10.7521923	total: 1.84s	remaining: 74.9ms
961:	learn: 10.7488251	total: 1.85s	remaining: 73ms
962:	learn: 10.7468294	total: 1.85

145:	learn: 14.6628341	total: 237ms	remaining: 1.39s
146:	learn: 14.6506636	total: 239ms	remaining: 1.39s
147:	learn: 14.6371700	total: 241ms	remaining: 1.39s
148:	learn: 14.6332343	total: 242ms	remaining: 1.38s
149:	learn: 14.6215759	total: 244ms	remaining: 1.38s
150:	learn: 14.6196021	total: 245ms	remaining: 1.37s
151:	learn: 14.6053103	total: 246ms	remaining: 1.37s
152:	learn: 14.5890625	total: 248ms	remaining: 1.37s
153:	learn: 14.5801924	total: 249ms	remaining: 1.37s
154:	learn: 14.5655017	total: 251ms	remaining: 1.37s
155:	learn: 14.5554103	total: 253ms	remaining: 1.37s
156:	learn: 14.5484010	total: 254ms	remaining: 1.36s
157:	learn: 14.5330736	total: 256ms	remaining: 1.36s
158:	learn: 14.5243954	total: 257ms	remaining: 1.36s
159:	learn: 14.5136213	total: 259ms	remaining: 1.36s
160:	learn: 14.5064155	total: 261ms	remaining: 1.36s
161:	learn: 14.4955887	total: 262ms	remaining: 1.36s
162:	learn: 14.4880507	total: 264ms	remaining: 1.35s
163:	learn: 14.4772060	total: 265ms	remaining:

379:	learn: 12.9689710	total: 624ms	remaining: 1.02s
380:	learn: 12.9655622	total: 626ms	remaining: 1.02s
381:	learn: 12.9585904	total: 628ms	remaining: 1.01s
382:	learn: 12.9572896	total: 629ms	remaining: 1.01s
383:	learn: 12.9558394	total: 631ms	remaining: 1.01s
384:	learn: 12.9528025	total: 632ms	remaining: 1.01s
385:	learn: 12.9398395	total: 634ms	remaining: 1.01s
386:	learn: 12.9342010	total: 636ms	remaining: 1.01s
387:	learn: 12.9302559	total: 637ms	remaining: 1s
388:	learn: 12.9224424	total: 639ms	remaining: 1s
389:	learn: 12.9175605	total: 641ms	remaining: 1s
390:	learn: 12.9093770	total: 642ms	remaining: 1s
391:	learn: 12.9035039	total: 644ms	remaining: 998ms
392:	learn: 12.8958701	total: 645ms	remaining: 997ms
393:	learn: 12.8868712	total: 647ms	remaining: 995ms
394:	learn: 12.8798401	total: 649ms	remaining: 994ms
395:	learn: 12.8715710	total: 650ms	remaining: 992ms
396:	learn: 12.8646707	total: 652ms	remaining: 990ms
397:	learn: 12.8549375	total: 653ms	remaining: 988ms
398:	

595:	learn: 11.7153957	total: 1.01s	remaining: 684ms
596:	learn: 11.7073964	total: 1.01s	remaining: 683ms
597:	learn: 11.7045813	total: 1.01s	remaining: 681ms
598:	learn: 11.7032327	total: 1.01s	remaining: 679ms
599:	learn: 11.6927856	total: 1.02s	remaining: 678ms
600:	learn: 11.6869437	total: 1.02s	remaining: 676ms
601:	learn: 11.6822101	total: 1.02s	remaining: 674ms
602:	learn: 11.6809632	total: 1.02s	remaining: 672ms
603:	learn: 11.6797137	total: 1.02s	remaining: 670ms
604:	learn: 11.6694519	total: 1.02s	remaining: 669ms
605:	learn: 11.6661298	total: 1.02s	remaining: 667ms
606:	learn: 11.6587196	total: 1.03s	remaining: 665ms
607:	learn: 11.6564748	total: 1.03s	remaining: 663ms
608:	learn: 11.6506706	total: 1.03s	remaining: 661ms
609:	learn: 11.6447827	total: 1.03s	remaining: 660ms
610:	learn: 11.6425140	total: 1.03s	remaining: 658ms
611:	learn: 11.6370096	total: 1.03s	remaining: 656ms
612:	learn: 11.6300766	total: 1.04s	remaining: 654ms
613:	learn: 11.6245588	total: 1.04s	remaining:

807:	learn: 10.8251866	total: 1.39s	remaining: 331ms
808:	learn: 10.8213084	total: 1.39s	remaining: 329ms
809:	learn: 10.8189002	total: 1.4s	remaining: 327ms
810:	learn: 10.8132222	total: 1.4s	remaining: 326ms
811:	learn: 10.8062383	total: 1.4s	remaining: 324ms
812:	learn: 10.8057389	total: 1.4s	remaining: 322ms
813:	learn: 10.8006803	total: 1.4s	remaining: 320ms
814:	learn: 10.7999411	total: 1.4s	remaining: 319ms
815:	learn: 10.7979442	total: 1.41s	remaining: 317ms
816:	learn: 10.7964521	total: 1.41s	remaining: 315ms
817:	learn: 10.7881292	total: 1.41s	remaining: 314ms
818:	learn: 10.7840867	total: 1.41s	remaining: 312ms
819:	learn: 10.7822464	total: 1.41s	remaining: 310ms
820:	learn: 10.7813770	total: 1.42s	remaining: 309ms
821:	learn: 10.7806816	total: 1.42s	remaining: 307ms
822:	learn: 10.7789975	total: 1.42s	remaining: 306ms
823:	learn: 10.7774344	total: 1.42s	remaining: 304ms
824:	learn: 10.7734764	total: 1.42s	remaining: 302ms
825:	learn: 10.7666996	total: 1.43s	remaining: 300ms

In [17]:
print("\nAverage performance of 5CV")
print("Metric\tavg\tstdev")
print("R^2\t%.2f\t%.2f" % (mean(r2_scores), stdev(r2_scores)))
print("RMSE\t%.2f\t%.2f" % (mean(rmse_scores), stdev(rmse_scores)))


Average performance of 5CV
Metric	avg	stdev
R^2	0.56	0.02
RMSE	14.14	0.18


In [18]:
# The "product" strategy
# Random Forest Regression

In [19]:
unique_inds = data['Ind'].unique()

In [20]:
for i in range(10):
    ind_train, ind_test = train_test_split(unique_inds, test_size=0.20, random_state=i)

    train_indices = data[data['Ind'].isin(ind_train)].index
    test_indices = data[data['Ind'].isin(ind_test)].index

    x_train, y_train = X.loc[train_indices].values, y.loc[train_indices].values
    x_test, y_test = X.loc[test_indices].values, y.loc[test_indices].values

    model = RandomForestRegressor(n_estimators=800, max_depth=8)
    model.fit(x_train, y_train)
    y_pred = model.predict(x_test)

    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    rmse_scores.append(rmse)

    r2 = r2_score(y_test, y_pred)
    r2_scores.append(r2)

    print(f"Iteration {i}: RMSE = {rmse:.3f}, R2 = {r2:.3f}")
    
print("\nAverage performance of test set at 10 split")
print("Metric\tavg\tstdev")
print("R^2\t%.2f\t%.2f" % (mean(r2_scores), stdev(r2_scores)))
print("RMSE\t%.2f\t%.2f" % (mean(rmse_scores), stdev(rmse_scores)))

Iteration 0: RMSE = 13.192, R2 = 0.636
Iteration 1: RMSE = 13.103, R2 = 0.585
Iteration 2: RMSE = 15.501, R2 = 0.461
Iteration 3: RMSE = 14.266, R2 = 0.570
Iteration 4: RMSE = 13.488, R2 = 0.580
Iteration 5: RMSE = 13.558, R2 = 0.500
Iteration 6: RMSE = 13.912, R2 = 0.518
Iteration 7: RMSE = 15.949, R2 = 0.495
Iteration 8: RMSE = 14.904, R2 = 0.548
Iteration 9: RMSE = 14.849, R2 = 0.482

Average performance of test set at 10 split
Metric	avg	stdev
R^2	0.55	0.04
RMSE	14.21	0.70


In [21]:
# Statistics for the training set with 5CV

In [22]:
ind_train, ind_test = train_test_split(unique_inds, test_size=0.2, random_state=1)

In [23]:
train_indices = data[data['Ind'].isin(ind_train)].index
test_indices = data[data['Ind'].isin(ind_test)].index

x_train, y_train = X.loc[train_indices].values, y.loc[train_indices].values
x_test, y_test = X.loc[test_indices].values, y.loc[test_indices].values

In [24]:
kf = KFold(n_splits=5, shuffle=True, random_state=1)
rmse_scores = []
r2_scores = []

In [25]:
for train_index, test_index in kf.split(x_train):
    x_train_fold, x_val_fold = x_train[train_index], x_train[test_index]
    y_train_fold, y_val_fold = y_train[train_index], y_train[test_index]

    model = RandomForestRegressor(n_estimators=800, max_depth=8)
    model.fit(x_train_fold, y_train_fold)
    y_pred = model.predict(x_val_fold)

    rmse = np.sqrt(mean_squared_error(y_val_fold, y_pred))
    rmse_scores.append(rmse)

    r2 = r2_score(y_val_fold, y_pred)
    r2_scores.append(r2)

In [26]:
print('R^2 = ', round(np.mean(r2_scores), 2))
print('RMSE = ', round(np.mean(rmse_scores), 2))

R^2 =  0.57
RMSE =  14.15


In [27]:
# catBoost

In [28]:
for i in range(10):
    ind_train, ind_test = train_test_split(unique_inds, test_size=0.20, random_state=i)

    train_indices = data[data['Ind'].isin(ind_train)].index
    test_indices = data[data['Ind'].isin(ind_test)].index

    x_train, y_train = X.loc[train_indices].values, y.loc[train_indices].values
    x_test, y_test = X.loc[test_indices].values, y.loc[test_indices].values

    model = catboost.CatBoostRegressor(learning_rate=0.02, l2_leaf_reg=9.5, depth=7)
    model.fit(x_train, y_train)
    y_pred = model.predict(x_test)

    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    rmse_scores.append(rmse)

    r2 = r2_score(y_test, y_pred)
    r2_scores.append(r2)

    print(f"Iteration {i}: RMSE = {rmse:.3f}, R2 = {r2:.3f}")

0:	learn: 21.0481073	total: 3.25ms	remaining: 3.25s
1:	learn: 20.9212304	total: 6.25ms	remaining: 3.12s
2:	learn: 20.7749576	total: 8.9ms	remaining: 2.96s
3:	learn: 20.6600410	total: 11.1ms	remaining: 2.76s
4:	learn: 20.5196795	total: 15ms	remaining: 2.98s
5:	learn: 20.4015865	total: 17.4ms	remaining: 2.88s
6:	learn: 20.2876719	total: 19.9ms	remaining: 2.82s
7:	learn: 20.1890436	total: 21.9ms	remaining: 2.71s
8:	learn: 20.0984921	total: 24ms	remaining: 2.65s
9:	learn: 19.9654358	total: 26.2ms	remaining: 2.59s
10:	learn: 19.8455239	total: 28.1ms	remaining: 2.52s
11:	learn: 19.7453630	total: 30.1ms	remaining: 2.48s
12:	learn: 19.6305566	total: 32ms	remaining: 2.43s
13:	learn: 19.5110514	total: 33.8ms	remaining: 2.38s
14:	learn: 19.3987812	total: 35.8ms	remaining: 2.35s
15:	learn: 19.3007659	total: 37.6ms	remaining: 2.31s
16:	learn: 19.2165923	total: 39.6ms	remaining: 2.29s
17:	learn: 19.1231136	total: 41.4ms	remaining: 2.26s
18:	learn: 19.0203149	total: 43.1ms	remaining: 2.22s
19:	learn:

204:	learn: 14.0717720	total: 366ms	remaining: 1.42s
205:	learn: 14.0677406	total: 367ms	remaining: 1.42s
206:	learn: 14.0579261	total: 369ms	remaining: 1.41s
207:	learn: 14.0548716	total: 371ms	remaining: 1.41s
208:	learn: 14.0507210	total: 372ms	remaining: 1.41s
209:	learn: 14.0462683	total: 374ms	remaining: 1.41s
210:	learn: 14.0395924	total: 376ms	remaining: 1.4s
211:	learn: 14.0324943	total: 378ms	remaining: 1.4s
212:	learn: 14.0253197	total: 379ms	remaining: 1.4s
213:	learn: 14.0189272	total: 381ms	remaining: 1.4s
214:	learn: 14.0169381	total: 382ms	remaining: 1.39s
215:	learn: 14.0137712	total: 384ms	remaining: 1.39s
216:	learn: 14.0071186	total: 385ms	remaining: 1.39s
217:	learn: 14.0019009	total: 387ms	remaining: 1.39s
218:	learn: 13.9918751	total: 389ms	remaining: 1.39s
219:	learn: 13.9798276	total: 390ms	remaining: 1.38s
220:	learn: 13.9702961	total: 392ms	remaining: 1.38s
221:	learn: 13.9637007	total: 394ms	remaining: 1.38s
222:	learn: 13.9596538	total: 396ms	remaining: 1.3

451:	learn: 12.9672424	total: 757ms	remaining: 918ms
452:	learn: 12.9599232	total: 759ms	remaining: 916ms
453:	learn: 12.9587173	total: 760ms	remaining: 915ms
454:	learn: 12.9580152	total: 762ms	remaining: 913ms
455:	learn: 12.9513942	total: 764ms	remaining: 911ms
456:	learn: 12.9494827	total: 765ms	remaining: 909ms
457:	learn: 12.9482531	total: 767ms	remaining: 907ms
458:	learn: 12.9417785	total: 768ms	remaining: 906ms
459:	learn: 12.9354853	total: 770ms	remaining: 904ms
460:	learn: 12.9312856	total: 771ms	remaining: 902ms
461:	learn: 12.9272415	total: 773ms	remaining: 900ms
462:	learn: 12.9256083	total: 775ms	remaining: 899ms
463:	learn: 12.9245003	total: 777ms	remaining: 897ms
464:	learn: 12.9146380	total: 778ms	remaining: 895ms
465:	learn: 12.9139085	total: 780ms	remaining: 893ms
466:	learn: 12.9047283	total: 781ms	remaining: 892ms
467:	learn: 12.9037871	total: 783ms	remaining: 890ms
468:	learn: 12.9027335	total: 784ms	remaining: 888ms
469:	learn: 12.9008209	total: 786ms	remaining:

684:	learn: 11.9679527	total: 1.15s	remaining: 528ms
685:	learn: 11.9615099	total: 1.15s	remaining: 526ms
686:	learn: 11.9585504	total: 1.15s	remaining: 524ms
687:	learn: 11.9549580	total: 1.15s	remaining: 523ms
688:	learn: 11.9518022	total: 1.15s	remaining: 521ms
689:	learn: 11.9511122	total: 1.16s	remaining: 520ms
690:	learn: 11.9500620	total: 1.16s	remaining: 518ms
691:	learn: 11.9470107	total: 1.16s	remaining: 516ms
692:	learn: 11.9456897	total: 1.16s	remaining: 514ms
693:	learn: 11.9421419	total: 1.16s	remaining: 513ms
694:	learn: 11.9417813	total: 1.16s	remaining: 511ms
695:	learn: 11.9396605	total: 1.17s	remaining: 509ms
696:	learn: 11.9339704	total: 1.17s	remaining: 508ms
697:	learn: 11.9309336	total: 1.17s	remaining: 506ms
698:	learn: 11.9224961	total: 1.17s	remaining: 504ms
699:	learn: 11.9204818	total: 1.17s	remaining: 503ms
700:	learn: 11.9170512	total: 1.17s	remaining: 501ms
701:	learn: 11.9102975	total: 1.18s	remaining: 499ms
702:	learn: 11.9075160	total: 1.18s	remaining:

921:	learn: 11.2420927	total: 1.54s	remaining: 130ms
922:	learn: 11.2413635	total: 1.54s	remaining: 128ms
923:	learn: 11.2383626	total: 1.54s	remaining: 127ms
924:	learn: 11.2357370	total: 1.54s	remaining: 125ms
925:	learn: 11.2349035	total: 1.54s	remaining: 123ms
926:	learn: 11.2338295	total: 1.55s	remaining: 122ms
927:	learn: 11.2331645	total: 1.55s	remaining: 120ms
928:	learn: 11.2307042	total: 1.55s	remaining: 118ms
929:	learn: 11.2252114	total: 1.55s	remaining: 117ms
930:	learn: 11.2219159	total: 1.55s	remaining: 115ms
931:	learn: 11.2209854	total: 1.55s	remaining: 113ms
932:	learn: 11.2183763	total: 1.56s	remaining: 112ms
933:	learn: 11.2126299	total: 1.56s	remaining: 110ms
934:	learn: 11.2123107	total: 1.56s	remaining: 108ms
935:	learn: 11.2120819	total: 1.56s	remaining: 107ms
936:	learn: 11.2086968	total: 1.56s	remaining: 105ms
937:	learn: 11.2057119	total: 1.56s	remaining: 103ms
938:	learn: 11.2053823	total: 1.56s	remaining: 102ms
939:	learn: 11.2019817	total: 1.57s	remaining:

...

997:	learn: 10.6717111	total: 1.93s	remaining: 3.86ms
998:	learn: 10.6705540	total: 1.93s	remaining: 1.93ms
999:	learn: 10.6652572	total: 1.93s	remaining: 0us
Iteration 8: RMSE = 15.190, R2 = 0.530
0:	learn: 21.3221705	total: 2.61ms	remaining: 2.61s
1:	learn: 21.1882612	total: 4.61ms	remaining: 2.3s
2:	learn: 21.0648685	total: 6.33ms	remaining: 2.1s
3:	learn: 20.9072947	total: 8.07ms	remaining: 2.01s
4:	learn: 20.7582848	total: 9.7ms	remaining: 1.93s
5:	learn: 20.6139193	total: 11.3ms	remaining: 1.87s
6:	learn: 20.4828215	total: 13ms	remaining: 1.84s
7:	learn: 20.3395296	total: 14.7ms	remaining: 1.82s
8:	learn: 20.2016419	total: 16.4ms	remaining: 1.8s
9:	learn: 20.0677948	total: 18ms	remaining: 1.79s
10:	learn: 19.9278544	total: 19.7ms	remaining: 1.77s
11:	learn: 19.8129914	total: 21.3ms	remaining: 1.75s
12:	learn: 19.7048445	total: 22.8ms	remaining: 1.73s
13:	learn: 19.6009279	total: 24.4ms	remaining: 1.72s
14:	learn: 19.4864723	total: 26.1ms	remaining: 1.72s
15:	learn: 19.3928323	tot

204:	learn: 13.6332595	total: 346ms	remaining: 1.34s
205:	learn: 13.6231133	total: 347ms	remaining: 1.34s
206:	learn: 13.6121938	total: 349ms	remaining: 1.34s
207:	learn: 13.6037143	total: 351ms	remaining: 1.34s
208:	learn: 13.5933483	total: 352ms	remaining: 1.33s
209:	learn: 13.5869193	total: 354ms	remaining: 1.33s
210:	learn: 13.5726168	total: 356ms	remaining: 1.33s
211:	learn: 13.5627017	total: 357ms	remaining: 1.33s
212:	learn: 13.5571206	total: 359ms	remaining: 1.33s
213:	learn: 13.5549789	total: 361ms	remaining: 1.32s
214:	learn: 13.5487013	total: 363ms	remaining: 1.32s
215:	learn: 13.5424509	total: 364ms	remaining: 1.32s
216:	learn: 13.5349191	total: 366ms	remaining: 1.32s
217:	learn: 13.5278267	total: 367ms	remaining: 1.32s
218:	learn: 13.5188789	total: 369ms	remaining: 1.32s
219:	learn: 13.5139023	total: 371ms	remaining: 1.31s
220:	learn: 13.5049025	total: 373ms	remaining: 1.31s
221:	learn: 13.5035806	total: 373ms	remaining: 1.31s
222:	learn: 13.4963165	total: 375ms	remaining:

417:	learn: 12.5498546	total: 735ms	remaining: 1.02s
418:	learn: 12.5479335	total: 737ms	remaining: 1.02s
419:	learn: 12.5428791	total: 739ms	remaining: 1.02s
420:	learn: 12.5410734	total: 741ms	remaining: 1.02s
421:	learn: 12.5336497	total: 743ms	remaining: 1.02s
422:	learn: 12.5319970	total: 745ms	remaining: 1.01s
423:	learn: 12.5311615	total: 747ms	remaining: 1.01s
424:	learn: 12.5293669	total: 748ms	remaining: 1.01s
425:	learn: 12.5269705	total: 750ms	remaining: 1.01s
426:	learn: 12.5234574	total: 752ms	remaining: 1.01s
427:	learn: 12.5188448	total: 754ms	remaining: 1.01s
428:	learn: 12.5123270	total: 756ms	remaining: 1s
429:	learn: 12.5105775	total: 757ms	remaining: 1s
430:	learn: 12.5090921	total: 759ms	remaining: 1s
431:	learn: 12.5067234	total: 761ms	remaining: 1s
432:	learn: 12.5026724	total: 763ms	remaining: 999ms
433:	learn: 12.5008082	total: 765ms	remaining: 997ms
434:	learn: 12.4953278	total: 766ms	remaining: 995ms
435:	learn: 12.4894495	total: 768ms	remaining: 994ms
436:	

624:	learn: 11.9057013	total: 1.12s	remaining: 673ms
625:	learn: 11.9055096	total: 1.12s	remaining: 672ms
626:	learn: 11.9042017	total: 1.13s	remaining: 670ms
627:	learn: 11.9037760	total: 1.13s	remaining: 668ms
628:	learn: 11.9035805	total: 1.13s	remaining: 666ms
629:	learn: 11.8980587	total: 1.13s	remaining: 665ms
630:	learn: 11.8978142	total: 1.13s	remaining: 663ms
631:	learn: 11.8902386	total: 1.14s	remaining: 662ms
632:	learn: 11.8900697	total: 1.14s	remaining: 660ms
633:	learn: 11.8826927	total: 1.14s	remaining: 658ms
634:	learn: 11.8800908	total: 1.14s	remaining: 657ms
635:	learn: 11.8794213	total: 1.14s	remaining: 655ms
636:	learn: 11.8787122	total: 1.15s	remaining: 653ms
637:	learn: 11.8756785	total: 1.15s	remaining: 651ms
638:	learn: 11.8754855	total: 1.15s	remaining: 649ms
639:	learn: 11.8748190	total: 1.15s	remaining: 648ms
640:	learn: 11.8711870	total: 1.15s	remaining: 646ms
641:	learn: 11.8656585	total: 1.16s	remaining: 644ms
642:	learn: 11.8641247	total: 1.16s	remaining:

830:	learn: 11.4261185	total: 1.51s	remaining: 307ms
831:	learn: 11.4257857	total: 1.51s	remaining: 305ms
832:	learn: 11.4215104	total: 1.51s	remaining: 303ms
833:	learn: 11.4210214	total: 1.51s	remaining: 301ms
834:	learn: 11.4174129	total: 1.52s	remaining: 300ms
835:	learn: 11.4101829	total: 1.52s	remaining: 298ms
836:	learn: 11.4054279	total: 1.52s	remaining: 296ms
837:	learn: 11.4021695	total: 1.52s	remaining: 294ms
838:	learn: 11.4013130	total: 1.52s	remaining: 292ms
839:	learn: 11.4002136	total: 1.52s	remaining: 290ms
840:	learn: 11.3985874	total: 1.53s	remaining: 289ms
841:	learn: 11.3980645	total: 1.53s	remaining: 287ms
842:	learn: 11.3919101	total: 1.53s	remaining: 285ms
843:	learn: 11.3906489	total: 1.53s	remaining: 283ms
844:	learn: 11.3887518	total: 1.53s	remaining: 281ms
845:	learn: 11.3822971	total: 1.53s	remaining: 280ms
846:	learn: 11.3818313	total: 1.54s	remaining: 278ms
847:	learn: 11.3817251	total: 1.54s	remaining: 276ms
848:	learn: 11.3802598	total: 1.54s	remaining:

In [29]:
print("\nAverage performance of test set at 10 split")
print("Metric\tavg\tstdev")
print("R^2\t%.2f\t%.2f" % (mean(r2_scores), stdev(r2_scores)))
print("RMSE\t%.2f\t%.2f" % (mean(rmse_scores), stdev(rmse_scores)))


Average performance of test set at 10 split
Metric	avg	stdev
R^2	0.55	0.05
RMSE	14.17	1.17


In [30]:
# Statistics for the training set with 5CV

In [31]:
for train_index, test_index in kf.split(x_train):
    x_train_fold, x_val_fold = x_train[train_index], x_train[test_index]
    y_train_fold, y_val_fold = y_train[train_index], y_train[test_index]

    model = catboost.CatBoostRegressor(learning_rate=0.02, l2_leaf_reg=9.5, depth=7)
    model.fit(x_train_fold, y_train_fold)
    y_pred = model.predict(x_val_fold)

    rmse = np.sqrt(mean_squared_error(y_val_fold, y_pred))
    rmse_scores.append(rmse)

    r2 = r2_score(y_val_fold, y_pred)
    r2_scores.append(r2)

0:	learn: 21.3261064	total: 2.32ms	remaining: 2.32s
1:	learn: 21.1725735	total: 4.72ms	remaining: 2.36s
2:	learn: 21.0463899	total: 9.17ms	remaining: 3.05s
3:	learn: 20.9112002	total: 10.9ms	remaining: 2.71s
4:	learn: 20.7668256	total: 12.8ms	remaining: 2.54s
5:	learn: 20.6412157	total: 14.4ms	remaining: 2.39s
6:	learn: 20.4985201	total: 16ms	remaining: 2.27s
7:	learn: 20.3556799	total: 18.3ms	remaining: 2.27s
8:	learn: 20.2328429	total: 20ms	remaining: 2.2s
9:	learn: 20.1154289	total: 21.5ms	remaining: 2.13s
10:	learn: 19.9949450	total: 23.3ms	remaining: 2.09s
11:	learn: 19.8713606	total: 24.8ms	remaining: 2.04s
12:	learn: 19.7516151	total: 26.4ms	remaining: 2s
13:	learn: 19.6385383	total: 28ms	remaining: 1.97s
14:	learn: 19.5099602	total: 29.7ms	remaining: 1.95s
15:	learn: 19.4098051	total: 31.3ms	remaining: 1.93s
16:	learn: 19.3175416	total: 32.9ms	remaining: 1.9s
17:	learn: 19.2141711	total: 34.4ms	remaining: 1.88s
18:	learn: 19.1103223	total: 36.1ms	remaining: 1.86s
19:	learn: 19.

229:	learn: 13.5100435	total: 371ms	remaining: 1.24s
230:	learn: 13.5030259	total: 372ms	remaining: 1.24s
231:	learn: 13.4955643	total: 374ms	remaining: 1.24s
232:	learn: 13.4836070	total: 375ms	remaining: 1.24s
233:	learn: 13.4768939	total: 377ms	remaining: 1.23s
234:	learn: 13.4701621	total: 378ms	remaining: 1.23s
235:	learn: 13.4583249	total: 380ms	remaining: 1.23s
236:	learn: 13.4533049	total: 381ms	remaining: 1.23s
237:	learn: 13.4417165	total: 383ms	remaining: 1.23s
238:	learn: 13.4377440	total: 385ms	remaining: 1.22s
239:	learn: 13.4319096	total: 395ms	remaining: 1.25s
240:	learn: 13.4253126	total: 397ms	remaining: 1.25s
241:	learn: 13.4197732	total: 398ms	remaining: 1.25s
242:	learn: 13.4139910	total: 400ms	remaining: 1.25s
243:	learn: 13.4090289	total: 401ms	remaining: 1.24s
244:	learn: 13.4063413	total: 402ms	remaining: 1.24s
245:	learn: 13.3971829	total: 404ms	remaining: 1.24s
246:	learn: 13.3851332	total: 405ms	remaining: 1.24s
247:	learn: 13.3780904	total: 407ms	remaining:

385:	learn: 12.6331133	total: 642ms	remaining: 1.02s
386:	learn: 12.6315971	total: 644ms	remaining: 1.02s
387:	learn: 12.6304535	total: 646ms	remaining: 1.02s
388:	learn: 12.6291240	total: 647ms	remaining: 1.02s
389:	learn: 12.6268077	total: 648ms	remaining: 1.01s
390:	learn: 12.6243101	total: 650ms	remaining: 1.01s
391:	learn: 12.6161285	total: 651ms	remaining: 1.01s
392:	learn: 12.6149169	total: 653ms	remaining: 1.01s
393:	learn: 12.6104364	total: 654ms	remaining: 1.01s
394:	learn: 12.6060485	total: 656ms	remaining: 1s
395:	learn: 12.6024254	total: 657ms	remaining: 1s
396:	learn: 12.5983005	total: 659ms	remaining: 1s
397:	learn: 12.5960266	total: 660ms	remaining: 999ms
398:	learn: 12.5914096	total: 662ms	remaining: 997ms
399:	learn: 12.5900338	total: 663ms	remaining: 995ms
400:	learn: 12.5885667	total: 665ms	remaining: 993ms
401:	learn: 12.5871959	total: 666ms	remaining: 991ms
402:	learn: 12.5860088	total: 668ms	remaining: 990ms
403:	learn: 12.5781429	total: 670ms	remaining: 988ms
40

577:	learn: 11.8535207	total: 957ms	remaining: 699ms
578:	learn: 11.8502953	total: 959ms	remaining: 697ms
579:	learn: 11.8463393	total: 960ms	remaining: 695ms
580:	learn: 11.8455351	total: 962ms	remaining: 694ms
581:	learn: 11.8380147	total: 964ms	remaining: 692ms
582:	learn: 11.8306801	total: 965ms	remaining: 690ms
583:	learn: 11.8301344	total: 967ms	remaining: 689ms
584:	learn: 11.8237260	total: 968ms	remaining: 687ms
585:	learn: 11.8202805	total: 970ms	remaining: 685ms
586:	learn: 11.8173030	total: 971ms	remaining: 683ms
587:	learn: 11.8120550	total: 973ms	remaining: 682ms
588:	learn: 11.8101274	total: 974ms	remaining: 680ms
589:	learn: 11.8040032	total: 976ms	remaining: 678ms
590:	learn: 11.7984256	total: 978ms	remaining: 677ms
591:	learn: 11.7869443	total: 980ms	remaining: 675ms
592:	learn: 11.7847056	total: 982ms	remaining: 674ms
593:	learn: 11.7841339	total: 983ms	remaining: 672ms
594:	learn: 11.7837783	total: 985ms	remaining: 670ms
595:	learn: 11.7834884	total: 986ms	remaining:

736:	learn: 11.4024103	total: 1.23s	remaining: 439ms
737:	learn: 11.4021961	total: 1.23s	remaining: 437ms
738:	learn: 11.3951182	total: 1.23s	remaining: 435ms
739:	learn: 11.3943504	total: 1.23s	remaining: 434ms
740:	learn: 11.3931675	total: 1.24s	remaining: 432ms
741:	learn: 11.3926691	total: 1.24s	remaining: 430ms
742:	learn: 11.3888317	total: 1.24s	remaining: 428ms
743:	learn: 11.3835569	total: 1.24s	remaining: 427ms
744:	learn: 11.3792760	total: 1.24s	remaining: 425ms
745:	learn: 11.3745104	total: 1.24s	remaining: 423ms
746:	learn: 11.3743161	total: 1.24s	remaining: 422ms
747:	learn: 11.3741137	total: 1.25s	remaining: 420ms
748:	learn: 11.3736817	total: 1.25s	remaining: 418ms
749:	learn: 11.3707973	total: 1.25s	remaining: 417ms
750:	learn: 11.3664811	total: 1.25s	remaining: 415ms
751:	learn: 11.3649022	total: 1.25s	remaining: 413ms
752:	learn: 11.3643352	total: 1.25s	remaining: 412ms
753:	learn: 11.3569292	total: 1.26s	remaining: 410ms
754:	learn: 11.3521626	total: 1.26s	remaining:

...

79:	learn: 15.4561628	total: 141ms	remaining: 1.62s
80:	learn: 15.4217766	total: 143ms	remaining: 1.62s
81:	learn: 15.3944240	total: 145ms	remaining: 1.62s
82:	learn: 15.3656645	total: 146ms	remaining: 1.61s
83:	learn: 15.3373410	total: 148ms	remaining: 1.61s
84:	learn: 15.3079626	total: 149ms	remaining: 1.61s
85:	learn: 15.2784233	total: 151ms	remaining: 1.6s
86:	learn: 15.2417776	total: 152ms	remaining: 1.6s
87:	learn: 15.2092016	total: 154ms	remaining: 1.59s
88:	learn: 15.1733151	total: 156ms	remaining: 1.6s
89:	learn: 15.1490345	total: 157ms	remaining: 1.59s
90:	learn: 15.1197948	total: 159ms	remaining: 1.59s
91:	learn: 15.0894804	total: 161ms	remaining: 1.58s
92:	learn: 15.0576317	total: 162ms	remaining: 1.58s
93:	learn: 15.0278876	total: 164ms	remaining: 1.58s
94:	learn: 14.9989357	total: 165ms	remaining: 1.57s
95:	learn: 14.9745245	total: 169ms	remaining: 1.59s
96:	learn: 14.9515056	total: 171ms	remaining: 1.59s
97:	learn: 14.9265472	total: 172ms	remaining: 1.59s
98:	learn: 14.8

239:	learn: 13.1314422	total: 410ms	remaining: 1.3s
240:	learn: 13.1230491	total: 412ms	remaining: 1.3s
241:	learn: 13.1178735	total: 414ms	remaining: 1.3s
242:	learn: 13.1129122	total: 416ms	remaining: 1.29s
243:	learn: 13.1090086	total: 417ms	remaining: 1.29s
244:	learn: 13.1002994	total: 419ms	remaining: 1.29s
245:	learn: 13.0876892	total: 421ms	remaining: 1.29s
246:	learn: 13.0750679	total: 422ms	remaining: 1.29s
247:	learn: 13.0717182	total: 424ms	remaining: 1.28s
248:	learn: 13.0672582	total: 426ms	remaining: 1.28s
249:	learn: 13.0600411	total: 427ms	remaining: 1.28s
250:	learn: 13.0504034	total: 429ms	remaining: 1.28s
251:	learn: 13.0474209	total: 430ms	remaining: 1.28s
252:	learn: 13.0369126	total: 432ms	remaining: 1.27s
253:	learn: 13.0298214	total: 434ms	remaining: 1.27s
254:	learn: 13.0242032	total: 435ms	remaining: 1.27s
255:	learn: 13.0168160	total: 437ms	remaining: 1.27s
256:	learn: 13.0124045	total: 439ms	remaining: 1.27s
257:	learn: 13.0065215	total: 440ms	remaining: 1.

420:	learn: 12.1335862	total: 722ms	remaining: 994ms
421:	learn: 12.1316407	total: 724ms	remaining: 992ms
422:	learn: 12.1280200	total: 726ms	remaining: 990ms
423:	learn: 12.1223369	total: 728ms	remaining: 989ms
424:	learn: 12.1194962	total: 730ms	remaining: 987ms
425:	learn: 12.1164797	total: 732ms	remaining: 986ms
426:	learn: 12.1111143	total: 733ms	remaining: 984ms
427:	learn: 12.1088578	total: 735ms	remaining: 982ms
428:	learn: 12.1069489	total: 736ms	remaining: 980ms
429:	learn: 12.1007181	total: 738ms	remaining: 979ms
430:	learn: 12.0996612	total: 740ms	remaining: 977ms
431:	learn: 12.0943046	total: 742ms	remaining: 975ms
432:	learn: 12.0888549	total: 743ms	remaining: 973ms
433:	learn: 12.0865754	total: 745ms	remaining: 972ms
434:	learn: 12.0845087	total: 747ms	remaining: 970ms
435:	learn: 12.0794952	total: 748ms	remaining: 968ms
436:	learn: 12.0770232	total: 750ms	remaining: 966ms
437:	learn: 12.0645137	total: 751ms	remaining: 964ms
438:	learn: 12.0634164	total: 753ms	remaining:

614:	learn: 11.1956544	total: 1.11s	remaining: 697ms
615:	learn: 11.1909845	total: 1.12s	remaining: 696ms
616:	learn: 11.1818356	total: 1.12s	remaining: 694ms
617:	learn: 11.1801913	total: 1.12s	remaining: 692ms
618:	learn: 11.1676869	total: 1.12s	remaining: 690ms
619:	learn: 11.1625765	total: 1.12s	remaining: 688ms
620:	learn: 11.1555327	total: 1.12s	remaining: 687ms
621:	learn: 11.1525793	total: 1.13s	remaining: 685ms
622:	learn: 11.1495850	total: 1.13s	remaining: 683ms
623:	learn: 11.1470376	total: 1.13s	remaining: 681ms
624:	learn: 11.1426482	total: 1.13s	remaining: 679ms
625:	learn: 11.1382322	total: 1.13s	remaining: 677ms
626:	learn: 11.1364120	total: 1.14s	remaining: 675ms
627:	learn: 11.1361260	total: 1.14s	remaining: 673ms
628:	learn: 11.1300656	total: 1.14s	remaining: 672ms
629:	learn: 11.1290355	total: 1.14s	remaining: 670ms
630:	learn: 11.1247174	total: 1.14s	remaining: 668ms
631:	learn: 11.1236384	total: 1.14s	remaining: 666ms
632:	learn: 11.1233583	total: 1.15s	remaining:

838:	learn: 10.4539180	total: 1.5s	remaining: 288ms
839:	learn: 10.4523924	total: 1.5s	remaining: 286ms
840:	learn: 10.4508675	total: 1.5s	remaining: 285ms
841:	learn: 10.4463460	total: 1.51s	remaining: 283ms
842:	learn: 10.4452775	total: 1.51s	remaining: 281ms
843:	learn: 10.4434662	total: 1.51s	remaining: 279ms
844:	learn: 10.4357346	total: 1.51s	remaining: 278ms
845:	learn: 10.4346657	total: 1.52s	remaining: 276ms
846:	learn: 10.4344572	total: 1.52s	remaining: 274ms
847:	learn: 10.4334728	total: 1.52s	remaining: 273ms
848:	learn: 10.4269510	total: 1.52s	remaining: 271ms
849:	learn: 10.4256562	total: 1.53s	remaining: 269ms
850:	learn: 10.4251222	total: 1.53s	remaining: 268ms
851:	learn: 10.4224462	total: 1.53s	remaining: 266ms
852:	learn: 10.4182501	total: 1.53s	remaining: 264ms
853:	learn: 10.4121335	total: 1.53s	remaining: 262ms
854:	learn: 10.4094545	total: 1.54s	remaining: 261ms
855:	learn: 10.4086310	total: 1.54s	remaining: 259ms
856:	learn: 10.4082015	total: 1.54s	remaining: 25

In [32]:
print('R^2 = ', round(np.mean(r2_scores), 2))
print('RMSE = ', round(np.mean(rmse_scores), 2))

R^2 =  0.55
RMSE =  14.14
